In [1]:
import pandas as pd
import re
import numpy as np
import matplotlib.pyplot as plt
from nltk.corpus import stopwords
from nltk.stem import PorterStemmer
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.pipeline import Pipeline
from sklearn.metrics import classification_report, confusion_matrix
from sklearn.model_selection import train_test_split
from sklearn.feature_selection import SelectKBest, chi2
from sklearn.ensemble import RandomForestClassifier
from sklearn.neighbors import KNeighborsClassifier
from sklearn.linear_model import LogisticRegression
import pickle
%matplotlib inline

In [2]:
import seaborn as sns
import matplotlib.pyplot as plt

In [3]:
from sklearn.preprocessing import OneHotEncoder 
from sklearn.preprocessing import LabelEncoder

# Explore and understand the data

In [4]:
# Read the different files.
data_dict = pd.read_csv('/Users/princessiria/Desktop/BigDataPrincess/widsdatathon2021/DataDictionaryWiDS2021.csv')
train_df = pd.read_csv('/Users/princessiria/Desktop/BigDataPrincess/widsdatathon2021/TrainingWiDS2021.csv')
unlabelled_df = pd.read_csv('/Users/princessiria/Desktop/BigDataPrincess/widsdatathon2021/UnlabeledWiDS2021.csv')

In [5]:
data_dict.head()

Category     Variable Name     Unit of Measure Data Type  \
0   identifier      encounter_id                None   integer   
1   identifier       hospital_id                None   integer   
2  demographic               age               Years   numeric   
3  demographic               bmi  kilograms/metres^2    string   
4  demographic  elective_surgery                None    binary   

                                         Description Example  
0  Unique identifier associated with a patient un...    None  
1       Unique identifier associated with a hospital    None  
2           The age of the patient on unit admission    None  
3  The body mass index of the person on unit admi...    21.5  
4  Whether the patient was admitted to the hospit...       0

In [6]:
missing_count = train_df.isna().sum()
missing_df = (pd.concat([missing_count.rename('Missing count'),
                     missing_count.div(len(train_df))
                          .rename('Missing ratio')],axis = 1)
             .loc[missing_count.ne(0)])
missing_df

Missing count  Missing ratio
age                            4988       0.038323
bmi                            4490       0.034497
ethnicity                      1587       0.012193
gender                           66       0.000507
height                         2077       0.015958
...                             ...            ...
h1_arterial_ph_min           107849       0.828607
h1_arterial_po2_max          107445       0.825503
h1_arterial_po2_min          107445       0.825503
h1_pao2fio2ratio_max         113397       0.871232
h1_pao2fio2ratio_min         113397       0.871232

[160 rows x 2 columns]

In [7]:
# list the columns.
train_df.columns

Index(['Unnamed: 0', 'encounter_id', 'hospital_id', 'age', 'bmi',
       'elective_surgery', 'ethnicity', 'gender', 'height',
       'hospital_admit_source',
       ...
       'h1_pao2fio2ratio_max', 'h1_pao2fio2ratio_min', 'aids', 'cirrhosis',
       'hepatic_failure', 'immunosuppression', 'leukemia', 'lymphoma',
       'solid_tumor_with_metastasis', 'diabetes_mellitus'],
      dtype='object', length=181)

In [8]:
# Describe the data to see what it looks like
train_df.describe()

Unnamed: 0   encounter_id    hospital_id            age  \
count  130157.000000  130157.000000  130157.000000  125169.000000   
mean    65079.000000  213000.856519     106.102131      61.995103   
std     37573.233831   38109.828146      63.482277      16.822880   
min         1.000000  147000.000000       1.000000       0.000000   
25%     32540.000000  180001.000000      49.000000      52.000000   
50%     65079.000000  213014.000000     112.000000      64.000000   
75%     97618.000000  246002.000000     165.000000      75.000000   
max    130157.000000  279000.000000     204.000000      89.000000   

                 bmi  elective_surgery         height         icu_id  \
count  125667.000000     130157.000000  128080.000000  130157.000000   
mean       29.110260          0.189840     169.607219     662.428344   
std         8.262776          0.392176      10.833085     304.259843   
min        14.844926          0.000000     137.200000      82.000000   
25%        23.598006          0.000000     162.500000     427.000000   
50%        27.564749          0.000000     170.100000     653.000000   
75%        32.803127          0.000000     177.800000     969.000000   
max        67.814990          1.000000     195.590000    1111.000000   

       pre_icu_los_days  readmission_status  ...  h1_pao2fio2ratio_max  \
count     130157.000000            130157.0  ...          16760.000000   
mean           0.839933                 0.0  ...            247.525419   
std            2.485337                 0.0  ...            131.440167   
min           -0.250000                 0.0  ...             42.000000   
25%            0.045833                 0.0  ...            144.000000   
50%            0.155556                 0.0  ...            228.125000   
75%            0.423611                 0.0  ...            333.000000   
max          175.627778                 0.0  ...            720.000000   

       h1_pao2fio2ratio_min          aids      cirrhosis  hepatic_failure  \
count          16760.000000  130157.00000  130157.000000    130157.000000   
mean             239.617358       0.00103       0.016081         0.013599   
std              128.562211       0.03207       0.125786         0.115819   
min               38.000000       0.00000       0.000000         0.000000   
25%              138.000000       0.00000       0.000000         0.000000   
50%              218.750000       0.00000       0.000000         0.000000   
75%              324.000000       0.00000       0.000000         0.000000   
max              654.813793       1.00000       1.000000         1.000000   

       immunosuppression       leukemia       lymphoma  \
count      130157.000000  130157.000000  130157.000000   
mean            0.025669       0.007307       0.004187   
std             0.158146       0.085166       0.064574   
min             0.000000       0.000000       0.000000   
25%             0.000000       0.000000       0.000000   
50%             0.000000       0.000000       0.000000   
75%             0.000000       0.000000       0.000000   
max             1.000000       1.000000       1.000000   

       solid_tumor_with_metastasis  diabetes_mellitus  
count                130157.000000      130157.000000  
mean                      0.020852           0.216285  
std                       0.142888           0.411712  
min                       0.000000           0.000000  
25%                       0.000000           0.000000  
50%                       0.000000           0.000000  
75%                       0.000000           0.000000  
max                       1.000000           1.000000  

[8 rows x 175 columns]

# Vizualize and see relationships

In [ ]:
plt.figure(figsize = (16,8))
plt.title('ethnicity', size = 20)
sns.countplot(y ='ethnicity', data = train_df);

In [ ]:
plt.figure(figsize = (16,8))
plt.title('Hospital Admit Source', size = 20)
sns.countplot(y ='hospital_admit_source', data = train_df);

# Data Cleaning Null Values

In [9]:
# Drop unused columns
train_df = train_df.drop(columns=['Unnamed: 0'])

In [10]:
# fill the NAN values
dt_i=[]
dt_fl=[]
dt_o=[]
for col in train_df.columns:
    x=train_df[col].dtype
    if x=='int64':
        dt_i.append(col)
    elif x=='float64':
        dt_fl.append(col)
    else:
        dt_o.append(col)

In [11]:
dt_fl.append("diabetes_mellitus")
train_df[np.intersect1d(train_df.columns, dt_fl)].corr().style.background_gradient(cmap='Oranges')

In [12]:
dt_fl.remove("diabetes_mellitus")
dt_i.remove("diabetes_mellitus")

In [13]:
import dask.dataframe as dd
from dask.dataframe.utils import make_meta

In [14]:
train_df = pd.DataFrame(train_df)
unlabelled_df = pd.DataFrame(unlabelled_df)

In [15]:
train_df[dt_o].isna().sum()

ethnicity                 1587
gender                      66
hospital_admit_source    33198
icu_admit_source           240
icu_stay_type                0
icu_type                     0
dtype: int64

In [16]:
train_df[dt_o] = train_df[dt_o].fillna("")
train_df[dt_o].isna().sum()

ethnicity                0
gender                   0
hospital_admit_source    0
icu_admit_source         0
icu_stay_type            0
icu_type                 0
dtype: int64

In [17]:
unlabelled_df[dt_o].isna().sum()

ethnicity                 204
gender                      5
hospital_admit_source    2733
icu_admit_source           25
icu_stay_type               0
icu_type                    0
dtype: int64

In [18]:
unlabelled_df[dt_o] = unlabelled_df[dt_o].fillna("")
unlabelled_df[dt_o].isna().sum()

ethnicity                0
gender                   0
hospital_admit_source    0
icu_admit_source         0
icu_stay_type            0
icu_type                 0
dtype: int64

In [19]:
train_df[dt_i] = train_df[dt_i].fillna(value=0)
unlabelled_df[dt_i] = unlabelled_df[dt_i].fillna(value=0)

train_df[dt_fl] = train_df[dt_fl].fillna(value=0)
unlabelled_df[dt_fl] = unlabelled_df[dt_fl].fillna(value=0)

# Model Section

In [20]:
train_df_without = train_df.drop(columns=['diabetes_mellitus'], axis=1)

In [21]:
# train_df_without = train_df.drop(columns=['encounter_id'], axis=1)

In [22]:
train_df_without.shape

(130157, 179)

In [23]:
le = LabelEncoder()
train_df_without['ethnicity'] = le.fit_transform(train_df_without.ethnicity.astype(str))
train_df_without['gender'] = le.fit_transform(train_df_without.gender.astype(str))
train_df_without['hospital_admit_source'] = le.fit_transform(train_df_without.hospital_admit_source.astype(str))

train_df_without['icu_admit_source'] = le.fit_transform(train_df_without.icu_admit_source.astype(str))
train_df_without['icu_stay_type'] = le.fit_transform(train_df_without.icu_stay_type.astype(str))
train_df_without['icu_type'] = le.fit_transform(train_df_without.icu_type.astype(str))


In [24]:
#split into training and test sets
X = train_df_without
Y = train_df['diabetes_mellitus']
X_train, X_test, y_train, y_test = train_test_split(X, Y, test_size=0.25, stratify=Y)

# Testing Randomforest Starts

In [ ]:
# try the randomforest model
# from sklearn.feature_extraction.text import TfidfVectorizer
# vect = TfidfVectorizer(sublinear_tf=True, norm='l2', ngram_range=(1,2))
# final_features = vect.fit_transform(train_df_without).toarray()
# final_features.shape


In [25]:
# try the randomforest model
pipeline2 = Pipeline([#('vec', vect),
                      #('chi', SelectKBest(chi2, k="all")),
                      ('clf', RandomForestClassifier())])

In [27]:
model2 = pipeline2.fit(X_train, y_train)

In [ ]:
ytest = np.array(y_test)

In [ ]:
print(classification_report(ytest, model2.predict(X_test)))
print(confusion_matrix(ytest, model2.predict(X_test)))

In [28]:
unlabelled_df['ethnicity'] = le.fit_transform(unlabelled_df.ethnicity.astype(str))
unlabelled_df['gender'] = le.fit_transform(unlabelled_df.gender.astype(str))
unlabelled_df['hospital_admit_source'] = le.fit_transform(unlabelled_df.hospital_admit_source.astype(str))

unlabelled_df['icu_admit_source'] = le.fit_transform(unlabelled_df.icu_admit_source.astype(str))
unlabelled_df['icu_stay_type'] = le.fit_transform(unlabelled_df.icu_stay_type.astype(str))
unlabelled_df['icu_type'] = le.fit_transform(unlabelled_df.icu_type.astype(str))

In [29]:
unlabelled_df = unlabelled_df.drop(columns=['Unnamed: 0'])

In [ ]:
# unlabelled_df = unlabelled_df.drop(columns=['encounter_id'])

In [ ]:
unlabelled_df['diabetes_mellitus'] = model2.predict(unlabelled_df)

In [ ]:
sub_df = unlabelled_df[['encounter_id', 'diabetes_mellitus']]
sub_df.to_csv('initiaRandomTest2.csv', index=False)

# Testing Randomforest ends

# Testing LogisticRegression starts

In [ ]:
model = LogisticRegression(solver='liblinear', random_state=0)

draft_model = model.fit(X_train, y_train)

In [ ]:
# Save the model
with open('LogisticRegression.pickle', 'wb') as f:
    pickle.dump(draft_model, f)
ytest = np.array(y_test)

In [ ]:
print(classification_report(ytest, draft_model.predict(X_test)))
print(confusion_matrix(ytest, draft_model.predict(X_test)))

# Test the model against the unlabelled_df

In [ ]:
# Clean the unlabelled_df just like the train_df

In [ ]:
unlabelled_df['ethnicity'] = le.fit_transform(unlabelled_df.ethnicity.astype(str))
unlabelled_df['gender'] = le.fit_transform(unlabelled_df.gender.astype(str))
unlabelled_df['hospital_admit_source'] = le.fit_transform(unlabelled_df.hospital_admit_source.astype(str))

unlabelled_df['icu_admit_source'] = le.fit_transform(unlabelled_df.icu_admit_source.astype(str))
unlabelled_df['icu_stay_type'] = le.fit_transform(unlabelled_df.icu_stay_type.astype(str))
unlabelled_df['icu_type'] = le.fit_transform(unlabelled_df.icu_type.astype(str))

In [ ]:
unlabelled_df = unlabelled_df.drop(columns=['Unnamed: 0'])

In [ ]:
unlabelled_df['diabetes_mellitus'] = draft_model.predict(unlabelled_df)

In [ ]:
see_1 = unlabelled_df[unlabelled_df['diabetes_mellitus'] == 1]

In [ ]:
# Write unlabelled_df to a csv file.
unlabelled_df.to_csv("draft_model_first_try.csv")

# Testing LogisticRegression ends

# KNeighborsClassifier begins

In [30]:
neigh = KNeighborsClassifier(n_neighbors=3)

In [31]:
model3 = neigh.fit(X_train, y_train)

In [ ]:
print(classification_report(ytest, model3.predict(X_test)))
print(confusion_matrix(ytest, model3.predict(X_test)))

In [ ]:
print(model3.predict_proba(X_test))

In [33]:
print(neigh.score(X_train, y_train))

0.8506100371861458


In [ ]:
# unlabelled_df.shape

# X_train.columns

In [32]:
unlabelled_df['diabetes_mellitus'] = model3.predict(unlabelled_df)

In [34]:
sub_df = unlabelled_df[['encounter_id', 'diabetes_mellitus']]
sub_df.to_csv('initiaKNN_1.csv', index=False)